In [1]:
import pandas as pd
import folium

In [2]:
merged = pd.read_csv("../local-data/merged_data.csv")
merged_updated = merged.copy()
merged_updated.loc[
    (merged_updated['STORE_TYPE'] == 'Other') & 
    (merged_updated['STORE_NAME'].str.lower().str.contains('dollar', case=False, na=False)), 
    'STORE_TYPE'
] = 'Discount Retail'

merged_updated.loc[
    (merged_updated['STORE_TYPE'] == 'Other') & 
    (merged_updated['STORE_NAME'].str.lower().str.contains('walgreens|cvs', case=False)), 
    'STORE_TYPE'
] = 'Pharmacy'

In [ ]:
#merged_updated.to_csv('C:/Users/macgl/OneDrive/Documents/priv-study/food-retail/local-data/foodRetailLocations.csv', index=False)

In [13]:
active_map = folium.Map(location=[32.7767, -96.7970], zoom_start=10)
store_types = merged_updated['STORE_TYPE'].unique()

store_type_colors = {
    'Convenience Store': 'red',
    'Discount Retail': 'darkblue',
    'Pharmacy': 'lightgreen',
    'Supermarket': 'blue',
    'Other': 'green',
    'Grocery Store': 'purple',
    'Super Store': 'orange',
    'Farmers and Markets': 'gray',
    'Specialty Store': 'pink',
    'Liquor Store': 'darkred',        
    'Confectionery': 'purple',        
    'Food Store': 'darkgreen',        
    'Produce Market': 'lightgreen',   
    'Seafood Market': 'cadetblue',    
    'Meat Market': 'darkred',
    'Bakery': 'lightblue',         
    'Specialty Food': 'darkgreen'
}

feature_groups = {}
for store_type in store_types:
    feature_groups[store_type] = folium.FeatureGroup(name=store_type)

for idx, row in merged_updated.iterrows():
    if pd.notna(row['LATITUDE']) and pd.notna(row['LONGITUDE']):  # Use uppercase
        store_type = row['STORE_TYPE']
        popup_text = f"<b>{row['STORE_NAME']}</b><br>Type: {store_type}"
        
        folium.Marker(
            location=[row['LATITUDE'], row['LONGITUDE']],  # Use uppercase
            popup=folium.Popup(popup_text, max_width=300),
            icon=folium.Icon(color=store_type_colors[store_type], icon='info-sign')
        ).add_to(feature_groups[store_type])

for fg in feature_groups.values():
    fg.add_to(active_map)

folium.LayerControl().add_to(active_map)

active_map